In [3]:
from pathlib import Path
import sys
import re
import pandas as pd
import shutil
import os
from multiprocessing import Pool
import prody
import pickle
ABPRED_DIR = Path.cwd().parent
if ABPRED_DIR not in sys.path:
    sys.path.append(str(ABPRED_DIR))
from AbPred.FoldX import FoldX
from modeller import *
from modeller.optimizers import molecular_dynamics, conjugate_gradients
from modeller.automodel import autosched


In [4]:
# vih benchmark dataframe
vih_dataframe = pd.read_csv('../data/HIV_escape_mutations.csv',sep="\t")
#ab_data_singleMut.sort_values('#Pdb',inplace=True)

# Paths data
PDBS_DIR = Path("../benchmark/VIH_modeller/")
vih_pdbs = list(PDBS_DIR.glob("*.pdb"))

In [5]:
vih_mutant_names = vih_dataframe.loc[vih_dataframe['Mutation_type']=='REVERSE']

In [6]:
vih_mutant_names

Mutation_type Chain Mutation  log10(Exptal)      Exptal  mCSM-AB_Pred
78        REVERSE     G     E54A       2.008643    101.0100         0.007
79        REVERSE     G     M62A       2.084512    120.4820         0.483
80        REVERSE     G     K64A       2.054460    112.3600         0.240
81        REVERSE     G     E69A       2.000043     99.0099         0.582
82        REVERSE     G     W79A       1.979273     94.3396         0.291
83        REVERSE     G     V87A       1.841942     68.4932         0.161
84        REVERSE     G     K88A       1.948018     87.7193         0.053
85        REVERSE     G     L89A       1.983347     95.2381         0.159
86        REVERSE     G    N163A       2.139835    136.9860        -0.173
87        REVERSE     G    N163K       2.030936    106.3830         0.075
88        REVERSE     G    N163T       2.122475    131.5790        -0.072
89        REVERSE     G    S165A       1.929591     84.0336        -0.189
90        REVERSE     G    T168A       1.991613     97.0874        -0.109
91        REVERSE     G    F176A       1.918906     81.9672         0.459
92        REVERSE     G    I179A       2.013010    102.0410        -0.110
93        REVERSE     G    R218A       1.918906     81.9672         0.004
94        REVERSE     G    S222A       2.084512    120.4820         0.593
95        REVERSE     G    T223A       2.399674    250.0000         0.748
96        REVERSE     G    N228A       2.445258    277.7780        -0.291
97        REVERSE     G    R239A       2.224448    166.6670         0.215
98        REVERSE     G    N242A       1.720543     51.5464         0.533
99        REVERSE     G    D245A       4.000043  10000.0000         2.292
100       REVERSE     G    N246A       2.176826    149.2540         1.637
101       REVERSE     G    K248A       2.164139    144.9280         0.034
102       REVERSE     G    T249A       2.105789    126.5820         0.887
103       REVERSE     G    T263S       2.026382    105.2630         0.015
104       REVERSE     G    R264A       1.944268     86.9565         0.131
105       REVERSE     G    N267A       1.850831     69.9301        -0.130
106       REVERSE     G    D290A       1.929591     84.0336         0.044
107       REVERSE     G    A294K       1.530132     32.8947        -0.125
..            ...   ...      ...            ...         ...           ...
126       REVERSE     G    W359A       1.747762     54.9451         0.612
127       REVERSE     G    R379A       1.878676     74.6269        -0.087
128       REVERSE     G    I380A       1.929591     84.0336        -0.047
129       REVERSE     G    K381A       1.878676     74.6269        -0.183
130       REVERSE     G    I383A       1.594549     38.3142         0.229
131       REVERSE     G    I384A       1.694988     48.5437        -0.071
132       REVERSE     G    N385A       2.133970    135.1350        -0.181
133       REVERSE     G    W387A       2.116840    129.8700         1.047
134       REVERSE     G    V390A       2.008643    101.0100         0.384
135       REVERSE     G    K392A       2.044892    109.8900         0.266
136       REVERSE     G    Y395A       2.017422    103.0930         0.318
137       REVERSE     G    I399A       1.891666     76.9231         0.263
138       REVERSE     G    T410A       2.278019    188.6790        -0.051
139       REVERSE     G    T415A       2.183313    151.5150         0.404
140       REVERSE     G    R416A       2.095019    123.4570         2.208
141       REVERSE     G    D417A       2.524179    333.3330         0.988
142       REVERSE     G    G418A       2.074257    117.6470         0.995
143       REVERSE     G    G419A       2.196591    156.2500         0.858
144       REVERSE     G    N421A       1.525994     32.5733         0.534
145       REVERSE     G    S423A       1.583351     37.3134         0.121
146       REVERSE     G    I427A       2.538860    344.8280         0.005
147       REVERSE     G    R429A       2.203386    158.7300         0.874
148     

# Parse only protein pdb data

In [9]:
for pdb in vih_pdbs:
    
    parser = prody.parsePDB(pdb)
    protein = parser.select("protein")
    prody.writePDB(str(pdb)[:-4]+".protein",protein)

In [10]:
vih_protein= list(PDBS_DIR.glob("*protein.pdb"))

#  Run mutation protocol by modeller

In [25]:
amino3to1dict = {'ALA': 'A','CYS': 'C','ASP': 'D','GLU': 'E','PHE': 'F','GLY': 'G',
                 'HIS': 'H','ILE': 'I','LYS': 'K','LEU': 'L','MET': 'M','ASN': 'N',
                 'PRO': 'P','GLN': 'Q','ARG': 'R','SER': 'S','THR': 'T','VAL': 'V',
                 'TRP': 'W','TYR': 'Y'}

def convertAAcode(m_splits):
    """Function to get the 3letters aa in amino3to1dict
    using the split_mutations() output"""
    for k,v in amino3to1dict.items():
        if v == m_splits[0]:
            return k
        
def split_mutations(mut_str):
    """Function to split a [mutation] string, searching the mutaion patter and return groups.
    Output is a list with 3 elements [wt_aa,aa_number,mut_aa] """
    
    search_mut = re.search("([A-Z])([0-9]+[A-Z]*)([A-Z])",mut_str,flags=re.I)
    m_splits = search_mut.groups()
    
    return list(m_splits)

In [42]:

def mutate_model(modelname,respos,restyp,chain,random_seed):
    
    #
    #  mutate_model.py
    #
    #     Usage:   python mutate_model.py modelname respos resname chain > logfile
    #
    #     Example: python mutate_model.py 1t29 1699 LEU A > 1t29.log
    #
    #
    #  Creates a single in silico point mutation to sidechain type and at residue position
    #  input by the user, in the structure whose file is modelname.pdb
    #  The conformation of the mutant sidechain is optimized by conjugate gradient and
    #  refined using some MD.
    #
    #  Note: if the model has no chain identifier, specify "" for the chain argument.
    #


    def optimize(atmsel, sched):
        #conjugate gradient
        for step in sched:
            step.optimize(atmsel, max_iterations=200, min_atom_shift=0.001)
        #md
        refine(atmsel)
        cg = conjugate_gradients()
        cg.optimize(atmsel, max_iterations=200, min_atom_shift=0.001)


    #molecular dynamics
    def refine(atmsel):
        # at T=1000, max_atom_shift for 4fs is cca 0.15 A.
        md = molecular_dynamics(cap_atom_shift=0.39, md_time_step=10.0,
                                md_return='FINAL')
        init_vel = True
        for (its, equil, temps) in ((200, 20, (150.0, 250.0, 400.0, 700.0, 1000.0,1500.0)),
                                    (2000, 200,
                                     (1500.0,1000.0, 800.0, 600.0, 500.0, 400.0, 300.0))):
            for temp in temps:
                md.optimize(atmsel, init_velocities=init_vel, temperature=temp,
                             max_iterations=its, equilibrate=equil)
                init_vel = False


    #use homologs and dihedral library for dihedral angle restraints
    def make_restraints(mdl1, aln):
        rsr = mdl1.restraints
        rsr.clear()
        s = selection(mdl1)
        for typ in ('stereo', 'phi-psi_binormal'):
            rsr.make(s, restraint_type=typ, aln=aln, spline_on_site=True)
        for typ in ('omega', 'chi1', 'chi2', 'chi3', 'chi4'):
            rsr.make(s, restraint_type=typ+'_dihedral', spline_range=4.0,
                    spline_dx=0.3, spline_min_points = 5, aln=aln,
                    spline_on_site=True)

    #first argument
    #modelname, respos, restyp, chain, = sys.argv[1:]


    log.verbose()

    # Set a different value for rand_seed to get a different final model
    env = environ(rand_seed=random_seed)

    env.io.hetatm = False
    #soft sphere potential
    env.edat.dynamic_sphere=False
    #lennard-jones potential (more accurate)
    env.edat.dynamic_lennard=True
    env.edat.contact_shell = 4.0
    env.edat.update_dynamic = 0.39

    # Read customized topology file with phosphoserines (or standard one)
    env.libs.topology.read(file='$(LIB)/top_heav.lib')

    # Read customized CHARMM parameter library with phosphoserines (or standard one)
    env.libs.parameters.read(file='$(LIB)/par.lib')


    # Read the original PDB file and copy its sequence to the alignment array:
    mdl1 = model(env, file=modelname)
    ali = alignment(env)
    ali.append_model(mdl1, atom_files=modelname, align_codes=modelname)

    #set up the mutate residue selection segment
    s = selection(mdl1.chains[chain].residues[respos])

    #perform the mutate residue operation
    s.mutate(residue_type=restyp)
    #get two copies of the sequence.  A modeller trick to get things set up
    ali.append_model(mdl1, align_codes=modelname)

    # Generate molecular topology for mutant
    mdl1.clear_topology()
    mdl1.generate_topology(ali[-1])


    # Transfer all the coordinates you can from the template native structure
    # to the mutant (this works even if the order of atoms in the native PDB
    # file is not standard):
    #here we are generating the model by reading the template coordinates
    mdl1.transfer_xyz(ali)

    # Build the remaining unknown coordinates
    mdl1.build(initialize_xyz=False, build_method='INTERNAL_COORDINATES')

    #yes model2 is the same file as model1.  It's a modeller trick.
    mdl2 = model(env, file=modelname)

    #required to do a transfer_res_numb
    #ali.append_model(mdl2, atom_files=modelname, align_codes=modelname)
    #transfers from "model 2" to "model 1"
    mdl1.res_num_from(mdl2,ali)

    #It is usually necessary to write the mutated sequence out and read it in
    #before proceeding, because not all sequence related information about MODEL
    #is changed by this command (e.g., internal coordinates, charges, and atom
    #types and radii are not updated).

    mdl1.write(file=modelname+restyp+respos+'.tmp')
    mdl1.read(file=modelname+restyp+respos+'.tmp')

    #set up restraints before computing energy
    #we do this a second time because the model has been written out and read in,
    #clearing the previously set restraints
    make_restraints(mdl1, ali)

    #a non-bonded pair has to have at least as many selected atoms
    mdl1.env.edat.nonbonded_sel_atoms=1

    sched = autosched.loop.make_for_model(mdl1)

    #only optimize the selected residue (in first pass, just atoms in selected
    #residue, in second pass, include nonbonded neighboring atoms)
    #set up the mutate residue selection segment
    s = selection(mdl1.chains[chain].residues[respos])

    mdl1.restraints.unpick_all()
    mdl1.restraints.pick(s)

    s.energy()

    s.randomize_xyz(deviation=4.0)

    mdl1.env.edat.nonbonded_sel_atoms=2
    optimize(s, sched)

    #feels environment (energy computed on pairs that have at least one member
    #in the selected)
    mdl1.env.edat.nonbonded_sel_atoms=1
    optimize(s, sched)

    s.energy()

    dope_energy = mdl1.assess_normalized_dope()
    #give a proper name
    mdl1.write(file=modelname[:-4]+"."+chain+respos+amino3to1dict[restyp]+'.wt.pdb')

    #delete the temporary file
    os.remove(modelname+restyp+respos+'.tmp')
    
    return dope_energy


In [57]:
def mainModmut(row):
    pdbid = 'VRC01'
    partners = 'LH_G'
    mutations = row.Mutation
    pdbname = '{}.protein.pdb'.format(pdbid,mutations)
    
    # get argument for mutate function
    modelfile = PDBS_DIR/Path(pdbname)
    mutation_split = split_mutations(mutations)
    # wildtype res
    restyp = convertAAcode(mutation_split[-1])
    respos = mutation_split[1]
    chain = row.Chain
    
    dope_energy =  mutate_model(modelname=str(modelfile.resolve()),restyp=restyp,chain=chain,respos=respos,random_seed=10)
    return dope_energy

def mainModwt(row):
    pdbid = 'VRC01'
    partners = 'LH_G'
    mutations = row.Mutation
    
     # get argument for mutate function
    mutation_split = split_mutations(mutations)
    # wildtype res
    restyp = convertAAcode(mutation_split[0])
    respos = mutation_split[1]
    chain = row.Chain
    
    pdbname = '{}.protein.{}.mut.pdb'.format(pdbid,chain+mutations[1:])
    modelfile = PDBS_DIR/Path(pdbname)
    
    dope_energy =  mutate_model(modelname=str(modelfile.resolve()),restyp=restyp,chain=chain,respos=respos,random_seed=10)
    return dope_energy

In [38]:
CWD = Path.cwd()

energy_mut = list()
try:
    #os.chdir('skempiAB-modeller')
    with Pool(12) as p:
        dope_energy = p.map(mainModmut, [row for i,row in vih_mutant_names.iterrows()])
        energy_mut.append(dope_energy)
finally:
    os.chdir(CWD)

openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}

              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
rdrdih__263_> Number of dihedral angle types         :        9
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Maximal number of dihedral angle optima:        3
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Maximal number of dihedral angle optima:        3
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Maximal number of dihedral angle optima:        3
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Maximal number of dihedral angle opti

openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTAL

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6137751    5993.897     5.853
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6140523    5996.604     5.856

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6131451    5987.745     5.847
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6141923    5997.972     5.857                              227     561     661     112       0


Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6140523    5996.604     5.856


Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6140523    5996.604     5.856
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6141923    5997.972     5.857

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6140523    5996.604     5.856
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6141923    5997.972     5.857
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:     



Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6153143    6008.929     5.868
Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6153993    6009.759     5.869


Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6153993    6009.759     5.869


Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6155251    6010.987     5.870
Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6152896    6008.688     5.868
Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6153993    6009.759     5.869
Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6152972    6008.762     5.868
Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6157195    6012.886     5.872



Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6153143    6008.929     5.868
Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6153993    6009.759     5.869
Dynamically allocated memory at

...

  serious non-bonded atom clash:   161  759   2.027

 #                     RESTRAINT_GROUP      NUM   NUMVI  NUMVP   RMS_1   RMS_2         MOL.PDF     S_i
------------------------------------------------------------------------------------------------------
 1 Bond length potential              :       6       0      0   0.021   0.021     0.77960       1.000
 2 Bond angle potential               :      10       0      0   3.205   3.205      2.0190       1.000
 3 Stereochemical cosine torsion poten:      13       0      0  69.196  69.196      3.9900       1.000
 4 Stereochemical improper torsion pot:       3       0      0   1.396   1.396     0.20329       1.000
 5 Soft-sphere overlap restraints     :       0       0      0   0.000   0.000      0.0000       1.000
 6 Lennard-Jones 6-12 potential       :      25       0      0   0.350   0.350     0.17286       1.000
 7 Coulomb point-point electrostatic p:       0       0      0   0.000   0.000      0.0000       1.000
 8 H-bonding potenti

randomi_496_> Amplitude is > 0; randomization is done.


>> ENERGY; Differences between the model's features and restraints:
Number of all residues in MODEL                   :      783
Number of all, selected real atoms                :     6089       5
Number of all, selected pseudo atoms              :        0       0
Number of all static, selected restraints         :    29884      37
COVALENT_CYS                                      :        F
NONBONDED_SEL_ATOMS                               :        1
Number of non-bonded pairs (excluding 1-2,1-3,1-4):       13
Dynamic pairs routine                             : 5, NATM_SEL x NATM double loop
Atomic shift for contacts update (UPDATE_DYNAMIC) :    0.390
LENNARD_JONES_SWITCH                              :    6.500   7.500
COULOMB_JONES_SWITCH                              :    6.500   7.500
RESIDUE_SPAN_RANGE                                :        0   99999
NLOGN_USE                                         :       15
CONTACT_SHEL






Summary of the restraint violations: 

   NUM     ... number of restraints.
   NUMVI   ... number of restraints with RVIOL > VIOL_REPORT_CUT[i].
   RVIOL   ... relative difference from the best value.
   NUMVP   ... number of restraints with -Ln(pdf) > VIOL_REPORT_CUT2[i].
   RMS_1   ... RMS(feature, minimally_violated_basis_restraint, NUMB).
   RMS_2   ... RMS(feature, best_value, NUMB).
   MOL.PDF ... scaled contribution to -Ln(Molecular pdf).

 #                     RESTRAINT_GROUP      NUM   NUMVI  NUMVP   RMS_1   RMS_2         MOL.PDF     S_i
------------------------------------------------------------------------------------------------------
 1 Bond length potential              :       6       0      0   0.011   0.011     0.20515       1.000
 2 Bond angle potential               :      10       0      0   2.915   2.915      1.5197       1.000
 3 Stereochemical cosine torsion poten:      13       0      0  67.153  67.153      3.7991       1.000
 4 Stereochemical improper to

COULOMB_JONES_SWITCH                              :    6.500   7.500
RESIDUE_SPAN_RANGE                                :        0   99999
NLOGN_USE                                         :       15
CONTACT_SHELL                                     :    4.000
DYNAMIC_PAIRS,_SPHERE,_COULOMB,_LENNARD,_MODELLER :        T       F       F       T       F

Dynamically allocated memory at  amaxrestraints [B,KiB,MiB]:     17168097   16765.719    16.373SPHERE_STDV                                       :    0.050

RADII_FACTOR                                      :    0.820
Current energy                                    :           8.5223




DISTANCE1:  0.00 2.10 2.20 2.30 2.40 2.50 2.60 2.70 2.80 2.90 3.00 3.10 3.20 3.30 3.40

Summary of the restraint violations: 

   NUM     ... number of restraints.
   NUMVI   ... number of restraints with RVIOL > VIOL_REPORT_CUT[i].
   RVIOL   ... relative difference from the best value.
   NUMVP   ... number of restraints with -Ln(pdf) > VIOL_REPORT_CU

COVALENT_CYS                                      :        F
NONBONDED_SEL_ATOMS                               :        1
Number of non-bonded pairs (excluding 1-2,1-3,1-4):  1222728
Dynamic pairs routine                             : 1, NATM x NATM double loop
Atomic shift for contacts update (UPDATE_DYNAMIC) :    0.390
LENNARD_JONES_SWITCH                              :    6.500   7.500
COULOMB_JONES_SWITCH                              :    6.500   7.500
RESIDUE_SPAN_RANGE                                :        1    9999
NLOGN_USE                                         :       15
CONTACT_SHELL                                     :   15.000
DYNAMIC_PAIRS,_SPHERE,_COULOMB,_LENNARD,_MODELLER :        T       F       F       F       T
SPHERE_STDV                                       :    0.050
RADII_FACTOR                                      :    0.820
Current energy                                    :      -83747.1797




<< end of ENERGY.
DOPE score               : -83747.179688
>

In [ ]:
with open('energy_dope_modellerSkempiABmut.pickle', 'wb') as f:
    # Pickle the 'data' dictionary using the highest protocol available.
    pickle.dump(energy_mut, f, pickle.HIGHEST_PROTOCOL)

In [4]:
skempiAB_mutant= list(PDBS_DIR.glob("*mut.pdb"))

## Model from mutant to wildtype

In [58]:
CWD = Path.cwd()

energy_wt = list()
try:
    #os.chdir('skempiAB-modeller')
    with Pool(12) as p:
        dope_energy = p.map(mainModwt, [row for i,row in vih_mutant_names.iterrows()])
        energy_wt.append(dope_energy)
finally:
    os.chdir(CWD)

openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           $(LIB)/restyp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.lib
rdresgr_266_> Number of residue groups:        2
openf___224_> Open           ${MODINSTALL9v20}/modlib/resgrp.l

              Maximal number of dihedral angle optima:        3
              Maximal number of dihedral angle optima:        3
rdrdih__263_> Number of dihedral angle types         :        9
              Maximal number of dihedral angle optima:        3
              Maximal number of dihedral angle optima:        3
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Maximal number of dihedral angle optima:        3
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Maximal number of dihedral angle optima:        3
openf___224_> Open           ${MODINSTALL9v20}/modlib/radii.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/radii.lib
              Dihedral angle names                   :  Alph Phi Psi Omeg chi1 chi2 chi3 chi4 chi5
              Dihedral angle

openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch2.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTALL9v20}/modlib/mnch3.lib
openf___224_> Open           ${MODINSTAL

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6141923    5997.972     5.857

read_pa_232_> parameters    BONDS   ANGLS  DIHEDS IMPROPS    MODE
openf___224_> Open           $(LIB)/par.lib

Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6137751    5993.897     5.853
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6140523    5996.604     5.856

openf___224_> Open           /Users/vfica/Documents/GitHub/AbPred/benchmark/VIH_modeller/VRC01.protein.G163A.mut.pdb

Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6152972    6008.762     5.868                              227     561     661     112       0


Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6103799    5960.741     5.821read_pa_232_> parameters    BONDS   ANGLS  DIHEDS IMPROPS    MODE


Dynamically allocated memory at  amaxparameters [B,KiB,MiB]:      6140523    5996.604     5.856
Dynamically allocated memory at  amaxparameters [B,KiB,MiB]

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6157155    6012.847     5.872
Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6164708    6020.223     5.879

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6171332    6026.691     5.885
Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6164708    6020.223     5.879
read_pa_232_> parameters    BONDS   ANGLS  DIHEDS IMPROPS    MODE




Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6171464    6026.820     5.886

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6160141    6015.763     5.875



Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6160201    6015.821     5.875                              227     561     661     112       0

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      6164906    6020.416     5.879

Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      6160201    6015.821     

...

Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      8554861    8354.356     8.159

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      8555158    8354.646     8.159

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      8564780    8364.043     8.168

Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      8564980    8364.238     8.168

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      8565430    8364.678     8.169

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      8579880    8378.789     8.182

Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      8580180    8379.082     8.183

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      8580855    8379.741     8.183

Dynamically allocated memory at amaxcoordinates [B,KiB,MiB]:      8602513    8400.892     8.204

Dynamically allocated memory at    amaxsequence [B,KiB,MiB]:      8602597    8400.974     8.204

Dynamically allocated memory a

make_re_417_> Restraint type to be calculated:  chi3_dihedral

Dynamically allocated memory at   amaxstructure [B,KiB,MiB]:     11966677   11686.208    11.412
openf___224_> Open           ${MODINSTALL9v20}/modlib/chi1234.bin
openf___224_> Open           ${MODINSTALL9v20}/modlib/chi3.mdt
getdata_643_> Protein accepted:  /Users/vfica/Documents/GitHub/AbPred/ben
getdata_289_> Proteins (all/accepted):        1        1
make_re_422_> Number of previous, current restraints         :    29606    29818
make_re_423_> Number of previous, current selected restraints:    28784    28996
make_re_417_> Restraint type to be calculated:  chi4_dihedral

Dynamically allocated memory at   amaxstructure [B,KiB,MiB]:     11966677   11686.208    11.412
openf___224_> Open           ${MODINSTALL9v20}/modlib/chi1234.bin
openf___224_> Open           ${MODINSTALL9v20}/modlib/chi4.mdt
mdtrsr__446W> A potential that relies on one protein is used, yet you have at
              least one known structure available. MD




report______> Distribution of short non-bonded contacts:

  serious non-bonded atom clash:   161  759   2.027
  serious non-bonded atom clash:   241  804   2.050
  serious non-bonded atom clash:  1139 1553   2.036
  serious non-bonded atom clash:  1707 3322   2.039
  serious non-bonded atom clash:  1851 2349   2.036
  serious non-bonded atom clash:  2687 3166   2.039
  serious non-bonded atom clash:  3415 3568   2.047
  serious non-bonded atom clash:  3740 5983   2.260
  serious non-bonded atom clash:  3741 5982   1.384
  serious non-bonded atom clash:  3741 5983   1.996
  serious non-bonded atom clash:  3741 5984   1.094
  serious non-bonded atom clash:  3742 5983   1.706
  serious non-bonded atom clash:  3743 5982   1.947
  serious non-bonded atom clash:  3743 5983   0.752
  serious non-bonded atom clash:  3744 5982   1.038
  serious non-bonded atom clash:  3744 5983   1.136
  serious non-bonded atom clash:  3744 5984   1.326
  serious non-bonded atom clash:  3745 5982   2.168
  s




report______> Distribution of short non-bonded contacts:

  serious non-bonded atom clash:   161  759   2.027
  serious non-bonded atom clash:   241  804   2.050
  serious non-bonded atom clash:  1139 1553   2.036
  serious non-bonded atom clash:  1707 3322   2.039
  serious non-bonded atom clash:  1851 2349   2.036
  serious non-bonded atom clash:  2687 3166   2.039
  serious non-bonded atom clash:  3415 3568   2.047
  serious non-bonded atom clash:  3938 4032   2.040
  serious non-bonded atom clash:  4139 4349   2.039
  serious non-bonded atom clash:  4207 4290   2.041
  serious non-bonded atom clash:  4725 4840   2.034
  serious non-bonded atom clash:  5214 5712   2.020
  serious non-bonded atom clash:  5271 5492   2.045

DISTANCE1:  0.00 2.10 2.20 2.30 2.40 2.50 2.60 2.70 2.80 2.90 3.00 3.10 3.20 3.30 3.40
DISTANCE2:  2.10 2.20 2.30 2.40 2.50 2.60 2.70 2.80 2.90 3.00 3.10 3.20 3.30 3.40 3.50
FREQUENCY:    13    0    0    0    0    0    1   17   91  210  288  380  544  716  924



28 NMR distance restraints 6 (X-Y)    :       0       0      0   0.000   0.000      0.0000       1.000
29 NMR distance restraints 7 (X-Y)    :       0       0      0   0.000   0.000      0.0000       1.000
30 Minimal distance restraints        :       0       0      0   0.000   0.000      0.0000       1.000
31 Non-bonded restraints              :       0       0      0   0.000   0.000      0.0000       1.000
32 Atomic accessibility restraints    :       0       0      0   0.000   0.000      0.0000       1.000
33 Atomic density restraints          :       0       0      0   0.000   0.000      0.0000       1.000
34 Absolute position restraints       :       0       0      0   0.000   0.000      0.0000       1.000
35 Dihedral angle difference restraint:       0       0      0   0.000   0.000      0.0000       1.000
36 GBSA implicit solvent potential    :       0       0      0   0.000   0.000      0.0000       1.000
37 EM density fitting potential       :       0       0      0   0.000   

In [ ]:
with open('energy_dope_modellerSkempiABwt.pickle', 'wb') as f:
    # Pickle the 'data' dictionary using the highest protocol available.
    pickle.dump(energy_wt, f, pickle.HIGHEST_PROTOCOL)

In [7]:
skempiAB_wt= list(PDBS_DIR.glob("*wt.pdb"))

In [9]:
skempiAB_wt

[PosixPath('../benchmark/VIH_modeller/VRC01.protein.G163A.mut.G163N.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G163K.mut.G163N.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G163T.mut.G163N.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G165A.mut.G165S.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G168A.mut.G168T.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G176A.mut.G176F.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G179A.mut.G179I.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G218A.mut.G218R.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G222A.mut.G222S.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G223A.mut.G223T.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G228A.mut.G228N.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G239A.mut.G239R.wt.pdb'),
 PosixPath('../benchmark/VIH_modeller/VRC01.protein.G242A.mut.G2

# Repair PDb mut

#### This was done on clsuter,  4 Repair run for each structure